In [2]:
import json
import os
from PIL import Image
import numpy as np
import shutil
import random
from PIL import Image, ImageDraw, ImageFont
import os
import cv2  

In [1]:
def convert_coco_to_yolo(coco_annotations_path, images_dir, output_dir):
    with open(coco_annotations_path, 'r') as f:
        data = json.load(f)
    
    os.makedirs(output_dir, exist_ok=True)

    for image_info in data['images']:
        image_id = image_info['id']
        image_filename = image_info['file_name']
        image_path = os.path.join(images_dir, image_filename)
        
        # Get image dimensions
        with Image.open(image_path) as img:
            img_width, img_height = img.size

        yolo_filename = os.path.splitext(image_filename)[0] + '.txt'
        yolo_path = os.path.join(output_dir, yolo_filename)

        with open(yolo_path, 'w') as yolo_file:
            for annotation in data['annotations']:
                if annotation['image_id'] == image_id:
                    category_id = annotation['category_id'] - 1  # YOLO uses 0-indexed classes
                    segmentation = annotation['segmentation'][0]  # Assuming single polygon per instance

                    # Convert segmentation to YOLO format
                    yolo_seg = []
                    for i in range(0, len(segmentation), 2):
                        x = segmentation[i] / img_width
                        y = segmentation[i+1] / img_height
                        yolo_seg.extend([x, y])

                    # Write to file
                    yolo_file.write(f"{category_id} {' '.join(map(str, yolo_seg))}\n")

    print(f"Conversion complete. YOLO format files saved in {output_dir}")

# Usage
coco_annotations_path = 'C:/Users/ds678/OneDrive - University of Sussex\SAF_Project/Instance_seg_labels/SAF22_COCO_CorentinDoche.json'
images_dir = 'C:/Users/ds678/OneDrive - University of Sussex/SAF_Project/Instance_seg_labels/images'
output_dir = 'C:/Users/ds678/OneDrive - University of Sussex/SAF_Project/Instance_seg_labels/output__SAF2022/labels'

convert_coco_to_yolo(coco_annotations_path, images_dir, output_dir)

Conversion complete. YOLO format files saved in C:/Users/ds678/OneDrive - University of Sussex/SAF_Project/Instance_seg_labels/output__SAF2022/labels


In [2]:
def split_data(images_dir, labels_dir, output_dir, split_ratio=0.8):
    # Create output directories
    train_img_dir = os.path.join(output_dir, 'train', 'images')
    train_label_dir = os.path.join(output_dir, 'train', 'labels')
    val_img_dir = os.path.join(output_dir, 'val', 'images')
    val_label_dir = os.path.join(output_dir, 'val', 'labels')
    
    os.makedirs(train_img_dir, exist_ok=True)
    os.makedirs(train_label_dir, exist_ok=True)
    os.makedirs(val_img_dir, exist_ok=True)
    os.makedirs(val_label_dir, exist_ok=True)
    
    # Get all image files
    image_files = [f for f in os.listdir(images_dir) if f.endswith(('.jpg', '.jpeg', '.png'))]
    
    # Shuffle the list of image files
    random.shuffle(image_files)
    
    # Calculate the split index
    split_index = int(len(image_files) * split_ratio)
    
    # Split and copy files
    for i, img_file in enumerate(image_files):
        img_path = os.path.join(images_dir, img_file)
        label_file = os.path.splitext(img_file)[0] + '.txt'
        label_path = os.path.join(labels_dir, label_file)
        
        if i < split_index:  # Training set
            shutil.copy(img_path, train_img_dir)
            if os.path.exists(label_path):
                shutil.copy(label_path, train_label_dir)
        else:  # Validation set
            shutil.copy(img_path, val_img_dir)
            if os.path.exists(label_path):
                shutil.copy(label_path, val_label_dir)
    
    print(f"Split complete. {split_index} images in training set, {len(image_files) - split_index} images in validation set.")

# Usage
images_dir = 'C:/Users/ds678/OneDrive - University of Sussex/SAF_Project/Instance_seg_labels/images'
labels_dir = 'C:/Users/ds678/OneDrive - University of Sussex/SAF_Project/Instance_seg_labels/output__SAF2022/labels'
output_dir = 'C:/Users/ds678/OneDrive - University of Sussex/SAF_Project/Instance_seg_labels/output__SAF2022'
split_ratio = 0.8  # 80% for training, 20% for validation

split_data(images_dir, labels_dir, output_dir, split_ratio)

Split complete. 42 images in training set, 11 images in validation set.


# YOLOv8n (NANO)

In [3]:
from ultralytics import YOLO

In [4]:
# Train YOLOv8n for segmentation
model = YOLO("yolov8n-seg.yaml")  # build a new model from YAML
model = YOLO("yolov8n-seg.pt")  # load a pretrained model (recommended for training)
model = YOLO("yolov8n-seg.yaml").load("yolov8n-seg.pt")  # build from YAML and transfer weights

Transferred 417/417 items from pretrained weights


# 100 Epoch

In [5]:
# Train the model on custom dataset
results=model.train(data="C:/Users/ds678/OneDrive - University of Sussex/SAF_Project/Instance_seg_labels/custom_data_PC - Copy.yaml", imgsz=1024, epochs=100, task='segment',batch=1, device=0, patience=0)  # Adjust the path and parameters as needed

New https://pypi.org/project/ultralytics/8.2.78 available  Update with 'pip install -U ultralytics'
Ultralytics YOLOv8.2.75  Python-3.10.14 torch-2.4.0+cu121 CUDA:0 (NVIDIA RTX A4000, 16376MiB)
engine\trainer: task=segment, mode=train, model=yolov8n-seg.yaml, data=C:/Users/ds678/OneDrive - University of Sussex/SAF_Project/Instance_seg_labels/custom_data_PC - Copy.yaml, epochs=100, time=None, patience=0, batch=1, imgsz=1024, save=True, save_period=-1, cache=False, device=0, workers=8, project=None, name=train46, exist_ok=False, pretrained=True, optimizer=auto, verbose=True, seed=0, deterministic=True, single_cls=False, rect=False, cos_lr=False, close_mosaic=10, resume=False, amp=True, fraction=1.0, profile=False, freeze=None, multi_scale=False, overlap_mask=True, mask_ratio=4, dropout=0.0, val=True, split=val, save_json=False, save_hybrid=False, conf=None, iou=0.7, max_det=300, half=False, dnn=False, plots=True, source=None, vid_stride=1, stream_buffer=False, visualize=False, augment=Fa

C:\ProgramData\anaconda3\envs\instance\lib\site-packages\ultralytics\engine\trainer.py:269: FutureWarning: `torch.cuda.amp.GradScaler(args...)` is deprecated. Please use `torch.amp.GradScaler('cuda', args...)` instead.
  self.scaler = torch.cuda.amp.GradScaler(enabled=self.amp)
train: Scanning C:\Users\ds678\Downloads\Instance_seg_labels\output_updated_last_time\train\labels.cache... 42 images, 0 backgrounds, 0 corrupt: 100%|██████████| 42/42 [00:00<?, ?it/s]
val: Scanning C:\Users\ds678\Downloads\Instance_seg_labels\output_updated_last_time\val\labels.cache... 11 images, 0 backgrounds, 0 corrupt: 100%|██████████| 11/11 [00:00<?, ?it/s]


Plotting labels to C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\runs\segment\train46\labels.jpg... 
optimizer: 'optimizer=auto' found, ignoring 'lr0=0.01' and 'momentum=0.937' and determining best 'optimizer', 'lr0' and 'momentum' automatically... 
optimizer: AdamW(lr=0.00125, momentum=0.9) with parameter groups 66 weight(decay=0.0), 77 weight(decay=0.0005), 76 bias(decay=0.0)
Image sizes 1024 train, 1024 val
Using 8 dataloader workers
Logging results to C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\runs\segment\train46
Starting training for 100 epochs...

      Epoch    GPU_mem   box_loss   seg_loss   cls_loss   dfl_loss  Instances       Size


      1/100     0.749G      3.164      4.229      7.498      1.255         39       1024: 100%|██████████| 42/42 [00:02<00:00, 18.72it/s]
                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95)     Mask(P          R      mAP50  mAP50-95): 100%|██████████| 6/6 [00:03<00:00,  1.51it/s]

                   all         11        225   0.000872      0.188     0.0352     0.0147   0.000872      0.188     0.0352      0.009


...

                   all         11        225       0.29      0.562       0.32      0.176       0.18      0.467      0.235      0.107

      Epoch    GPU_mem   box_loss   seg_loss   cls_loss   dfl_loss  Instances       Size


    100/100     0.786G      1.372      1.211      2.296     0.8721         79       1024: 100%|██████████| 42/42 [00:01<00:00, 28.32it/s]
                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95)     Mask(P          R      mAP50  mAP50-95): 100%|██████████| 6/6 [00:00<00:00, 35.71it/s]


                   all         11        225      0.282      0.552      0.424      0.249      0.191      0.466      0.362        0.2

100 epochs completed in 0.067 hours.
Optimizer stripped from C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\runs\segment\train46\weights\last.pt, 6.8MB
Optimizer stripped from C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\runs\segment\train46\weights\best.pt, 6.8MB

Validating C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\runs\segment\train46\weights\best.pt...
Ultralytics YOLOv8.2.75  Python-3.10.14 torch-2.4.0+cu121 CUDA:0 (NVIDIA RTX A4000, 16376MiB)
YOLOv8n-seg summary (fused): 195 layers, 3,258,844 parameters, 0 gradients, 12.0 GFLOPs


                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95)     Mask(P          R      mAP50  mAP50-95): 100%|██████████| 6/6 [00:00<00:00, 21.98it/s]


                   all         11        225      0.228      0.558       0.44      0.238      0.161      0.468      0.362      0.208
  ClassicalEvaporation          7        105      0.441      0.524      0.428      0.241      0.337      0.381      0.241     0.0723
    TransitionalMixing          8         61      0.335      0.689      0.351      0.219      0.258      0.492      0.257     0.0607
       DiffusiveMixing          6         55     0.0855     0.0182     0.0684     0.0263          0          0     0.0372     0.0141
                 Spray          4          4     0.0489          1      0.912      0.467      0.049          1      0.912      0.684
Speed: 0.6ms preprocess, 10.0ms inference, 0.0ms loss, 1.5ms postprocess per image
Results saved to C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\runs\segment\train46


# 500 Epoch

In [6]:
# Train the model on custom dataset
results=model.train(data="C:/Users/ds678/OneDrive - University of Sussex/SAF_Project/Instance_seg_labels/custom_data_PC - Copy.yaml", imgsz=1024, epochs=500, task='segment',batch=1, device=0, patience=0)  # Adjust the path and parameters as needed

New https://pypi.org/project/ultralytics/8.2.78 available  Update with 'pip install -U ultralytics'
Ultralytics YOLOv8.2.75  Python-3.10.14 torch-2.4.0+cu121 CUDA:0 (NVIDIA RTX A4000, 16376MiB)
engine\trainer: task=segment, mode=train, model=yolov8n-seg.yaml, data=C:/Users/ds678/OneDrive - University of Sussex/SAF_Project/Instance_seg_labels/custom_data_PC - Copy.yaml, epochs=500, time=None, patience=0, batch=1, imgsz=1024, save=True, save_period=-1, cache=False, device=0, workers=8, project=None, name=train462, exist_ok=False, pretrained=True, optimizer=auto, verbose=True, seed=0, deterministic=True, single_cls=False, rect=False, cos_lr=False, close_mosaic=10, resume=False, amp=True, fraction=1.0, profile=False, freeze=None, multi_scale=False, overlap_mask=True, mask_ratio=4, dropout=0.0, val=True, split=val, save_json=False, save_hybrid=False, conf=None, iou=0.7, max_det=300, half=False, dnn=False, plots=True, source=None, vid_stride=1, stream_buffer=False, visualize=False, augment=F

train: Scanning C:\Users\ds678\Downloads\Instance_seg_labels\output_updated_last_time\train\labels.cache... 42 images, 0 backgrounds, 0 corrupt: 100%|██████████| 42/42 [00:00<?, ?it/s]
val: Scanning C:\Users\ds678\Downloads\Instance_seg_labels\output_updated_last_time\val\labels.cache... 11 images, 0 backgrounds, 0 corrupt: 100%|██████████| 11/11 [00:00<?, ?it/s]


Plotting labels to C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\runs\segment\train462\labels.jpg... 
optimizer: 'optimizer=auto' found, ignoring 'lr0=0.01' and 'momentum=0.937' and determining best 'optimizer', 'lr0' and 'momentum' automatically... 
optimizer: AdamW(lr=0.00125, momentum=0.9) with parameter groups 66 weight(decay=0.0), 77 weight(decay=0.0005), 76 bias(decay=0.0)
Image sizes 1024 train, 1024 val
Using 8 dataloader workers
Logging results to C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\runs\segment\train462
Starting training for 500 epochs...

      Epoch    GPU_mem   box_loss   seg_loss   cls_loss   dfl_loss  Instances       Size


      1/500     0.744G      1.481      1.186      2.379     0.8943         39       1024: 100%|██████████| 42/42 [00:01<00:00, 23.32it/s]
                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95)     Mask(P          R      mAP50  mAP50-95): 100%|██████████| 6/6 [00:00<00:00, 35.71it/s]

                   all         11        225      0.224      0.562      0.324      0.188      0.158      0.456      0.237      0.129


...


      Epoch    GPU_mem   box_loss   seg_loss   cls_loss   dfl_loss  Instances       Size


    500/500     0.744G      1.005     0.6753     0.9298     0.8234         14       1024: 100%|██████████| 42/42 [00:02<00:00, 18.18it/s]
                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95)     Mask(P          R      mAP50  mAP50-95): 100%|██████████| 6/6 [00:00<00:00, 18.69it/s]


                   all         11        225      0.446      0.574      0.564      0.364      0.348      0.462      0.432      0.231

500 epochs completed in 0.300 hours.
Optimizer stripped from C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\runs\segment\train462\weights\last.pt, 6.9MB
Optimizer stripped from C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\runs\segment\train462\weights\best.pt, 6.9MB

Validating C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\runs\segment\train462\weights\best.pt...
Ultralytics YOLOv8.2.75  Python-3.10.14 torch-2.4.0+cu121 CUDA:0 (NVIDIA RTX A4000, 16376MiB)
YOLOv8n-seg summary (fused): 195 layers, 3,258,844 parameters, 0 gradients, 12.0 GFLOPs


                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95)     Mask(P          R      mAP50  mAP50-95): 100%|██████████| 6/6 [00:00<00:00, 14.71it/s]


                   all         11        225      0.464      0.528       0.58      0.401      0.353      0.442      0.444      0.255
  ClassicalEvaporation          7        105      0.608      0.476      0.528      0.346      0.444      0.333      0.312     0.0891
    TransitionalMixing          8         61      0.613      0.492      0.568       0.41      0.463      0.361      0.379      0.128
       DiffusiveMixing          6         55      0.336      0.145       0.23      0.129      0.201     0.0727     0.0909     0.0263
                 Spray          4          4      0.299          1      0.995      0.719      0.302          1      0.995      0.776
Speed: 2.5ms preprocess, 8.4ms inference, 0.0ms loss, 2.2ms postprocess per image
Results saved to C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\runs\segment\train462


# 1000 Epoch

In [7]:
# Train the model on custom dataset
results=model.train(data="C:/Users/ds678/OneDrive - University of Sussex/SAF_Project/Instance_seg_labels/custom_data_PC - Copy.yaml", imgsz=1024, epochs=1000, task='segment',batch=1, device=0, patience=0)  # Adjust the path and parameters as needed

New https://pypi.org/project/ultralytics/8.2.78 available  Update with 'pip install -U ultralytics'
Ultralytics YOLOv8.2.75  Python-3.10.14 torch-2.4.0+cu121 CUDA:0 (NVIDIA RTX A4000, 16376MiB)
engine\trainer: task=segment, mode=train, model=yolov8n-seg.yaml, data=C:/Users/ds678/OneDrive - University of Sussex/SAF_Project/Instance_seg_labels/custom_data_PC - Copy.yaml, epochs=1000, time=None, patience=0, batch=1, imgsz=1024, save=True, save_period=-1, cache=False, device=0, workers=8, project=None, name=train4622, exist_ok=False, pretrained=True, optimizer=auto, verbose=True, seed=0, deterministic=True, single_cls=False, rect=False, cos_lr=False, close_mosaic=10, resume=False, amp=True, fraction=1.0, profile=False, freeze=None, multi_scale=False, overlap_mask=True, mask_ratio=4, dropout=0.0, val=True, split=val, save_json=False, save_hybrid=False, conf=None, iou=0.7, max_det=300, half=False, dnn=False, plots=True, source=None, vid_stride=1, stream_buffer=False, visualize=False, augment

train: Scanning C:\Users\ds678\Downloads\Instance_seg_labels\output_updated_last_time\train\labels.cache... 42 images, 0 backgrounds, 0 corrupt: 100%|██████████| 42/42 [00:00<?, ?it/s]
val: Scanning C:\Users\ds678\Downloads\Instance_seg_labels\output_updated_last_time\val\labels.cache... 11 images, 0 backgrounds, 0 corrupt: 100%|██████████| 11/11 [00:00<?, ?it/s]


Plotting labels to C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\runs\segment\train4622\labels.jpg... 
optimizer: 'optimizer=auto' found, ignoring 'lr0=0.01' and 'momentum=0.937' and determining best 'optimizer', 'lr0' and 'momentum' automatically... 
optimizer: AdamW(lr=0.00125, momentum=0.9) with parameter groups 66 weight(decay=0.0), 77 weight(decay=0.0005), 76 bias(decay=0.0)
Image sizes 1024 train, 1024 val
Using 8 dataloader workers
Logging results to C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\runs\segment\train4622
Starting training for 1000 epochs...

      Epoch    GPU_mem   box_loss   seg_loss   cls_loss   dfl_loss  Instances       Size


     1/1000     0.744G      1.002     0.7267      0.947     0.8396         39       1024: 100%|██████████| 42/42 [00:02<00:00, 15.23it/s]
                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95)     Mask(P          R      mAP50  mAP50-95): 100%|██████████| 6/6 [00:00<00:00, 18.32it/s]

                   all         11        225      0.438      0.539      0.512      0.336      0.307      0.442      0.369      0.199


...

  1000/1000     0.768G      0.868     0.7613     0.5554     0.7947         15       1024: 100%|██████████| 42/42 [00:02<00:00, 15.92it/s]
                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95)     Mask(P          R      mAP50  mAP50-95): 100%|██████████| 6/6 [00:00<00:00, 19.67it/s]

                   all         11        225      0.491      0.551      0.542      0.346      0.439      0.411      0.388      0.213



1000 epochs completed in 0.888 hours.
Optimizer stripped from C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\runs\segment\train4622\weights\last.pt, 7.0MB
Optimizer stripped from C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\runs\segment\train4622\weights\best.pt, 6.9MB

Validating C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\runs\segment\train4622\weights\best.pt...
Ultralytics YOLOv8.2.75  Python-3.10.14 torch-2.4.0+cu121 CUDA:0 (NVIDIA RTX A4000, 16376MiB)
YOLOv8n-seg summary (fused): 195 layers, 3,258,844 parameters, 0 gradients, 12.0 GFLOPs


                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95)     Mask(P          R      mAP50  mAP50-95): 100%|██████████| 6/6 [00:00<00:00, 12.06it/s]


                   all         11        225      0.456      0.544      0.593      0.392      0.312      0.456      0.441      0.244
  ClassicalEvaporation          7        105      0.556      0.514       0.56      0.363      0.354      0.352      0.303     0.0941
    TransitionalMixing          8         61      0.635      0.475      0.596      0.418      0.404      0.344      0.331     0.0743
       DiffusiveMixing          6         55      0.406      0.187      0.219      0.129      0.263      0.127      0.134     0.0366
                 Spray          4          4      0.227          1      0.995      0.659      0.226          1      0.995      0.771
Speed: 1.2ms preprocess, 11.0ms inference, 0.0ms loss, 2.3ms postprocess per image
Results saved to C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\runs\segment\train4622


# 3000 Epoch

In [8]:
# Train the model on custom dataset
results=model.train(data="C:/Users/ds678/OneDrive - University of Sussex/SAF_Project/Instance_seg_labels/custom_data_PC - Copy.yaml", imgsz=1024, epochs=3000, task='segment',batch=1, device=0, patience=0)  # Adjust the path and parameters as needed

New https://pypi.org/project/ultralytics/8.2.78 available  Update with 'pip install -U ultralytics'
Ultralytics YOLOv8.2.75  Python-3.10.14 torch-2.4.0+cu121 CUDA:0 (NVIDIA RTX A4000, 16376MiB)
engine\trainer: task=segment, mode=train, model=yolov8n-seg.yaml, data=C:/Users/ds678/OneDrive - University of Sussex/SAF_Project/Instance_seg_labels/custom_data_PC - Copy.yaml, epochs=3000, time=None, patience=0, batch=1, imgsz=1024, save=True, save_period=-1, cache=False, device=0, workers=8, project=None, name=train46222, exist_ok=False, pretrained=True, optimizer=auto, verbose=True, seed=0, deterministic=True, single_cls=False, rect=False, cos_lr=False, close_mosaic=10, resume=False, amp=True, fraction=1.0, profile=False, freeze=None, multi_scale=False, overlap_mask=True, mask_ratio=4, dropout=0.0, val=True, split=val, save_json=False, save_hybrid=False, conf=None, iou=0.7, max_det=300, half=False, dnn=False, plots=True, source=None, vid_stride=1, stream_buffer=False, visualize=False, augmen

train: Scanning C:\Users\ds678\Downloads\Instance_seg_labels\output_updated_last_time\train\labels.cache... 42 images, 0 backgrounds, 0 corrupt: 100%|██████████| 42/42 [00:00<?, ?it/s]
val: Scanning C:\Users\ds678\Downloads\Instance_seg_labels\output_updated_last_time\val\labels.cache... 11 images, 0 backgrounds, 0 corrupt: 100%|██████████| 11/11 [00:00<?, ?it/s]


Plotting labels to C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\runs\segment\train46222\labels.jpg... 
optimizer: 'optimizer=auto' found, ignoring 'lr0=0.01' and 'momentum=0.937' and determining best 'optimizer', 'lr0' and 'momentum' automatically... 
optimizer: AdamW(lr=0.00125, momentum=0.9) with parameter groups 66 weight(decay=0.0), 77 weight(decay=0.0005), 76 bias(decay=0.0)
Image sizes 1024 train, 1024 val
Using 8 dataloader workers
Logging results to C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\runs\segment\train46222
Starting training for 3000 epochs...

      Epoch    GPU_mem   box_loss   seg_loss   cls_loss   dfl_loss  Instances       Size


     1/3000     0.747G      1.097     0.7766     0.9347     0.8447         39       1024: 100%|██████████| 42/42 [00:02<00:00, 15.28it/s]
                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95)     Mask(P          R      mAP50  mAP50-95): 100%|██████████| 6/6 [00:00<00:00, 18.99it/s]


                   all         11        225      0.475      0.521      0.593      0.387      0.333      0.432      0.443      0.241

      Epoch    GPU_mem   box_loss   seg_loss   cls_loss   dfl_loss  Instances       Size


...

  3000/3000      0.73G     0.6252     0.4487     0.3223     0.7737         20       1024: 100%|██████████| 42/42 [00:01<00:00, 28.06it/s]
                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95)     Mask(P          R      mAP50  mAP50-95): 100%|██████████| 6/6 [00:00<00:00, 38.22it/s]

                   all         11        225      0.579      0.515      0.559      0.359      0.484      0.404      0.419      0.212



3000 epochs completed in 2.615 hours.
Optimizer stripped from C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\runs\segment\train46222\weights\last.pt, 7.3MB
Optimizer stripped from C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\runs\segment\train46222\weights\best.pt, 7.2MB

Validating C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\runs\segment\train46222\weights\best.pt...
Ultralytics YOLOv8.2.75  Python-3.10.14 torch-2.4.0+cu121 CUDA:0 (NVIDIA RTX A4000, 16376MiB)
YOLOv8n-seg summary (fused): 195 layers, 3,258,844 parameters, 0 gradients, 12.0 GFLOPs


                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95)     Mask(P          R      mAP50  mAP50-95): 100%|██████████| 6/6 [00:00<00:00, 20.76it/s]


                   all         11        225      0.542      0.537      0.568      0.377      0.452      0.441      0.443      0.247
  ClassicalEvaporation          7        105      0.586      0.457      0.567      0.392      0.439      0.314      0.334      0.108
    TransitionalMixing          8         61      0.632      0.508       0.58      0.444      0.587      0.377      0.426      0.122
       DiffusiveMixing          6         55      0.412      0.182      0.231       0.14      0.209     0.0727      0.118     0.0476
                 Spray          4          4       0.54          1      0.895      0.532      0.574          1      0.895      0.712
Speed: 0.4ms preprocess, 10.9ms inference, 0.0ms loss, 1.5ms postprocess per image
Results saved to C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\runs\segment\train46222


In [10]:
!pip install wandb

  Using cached click-8.1.7-py3-none-any.whl.metadata (3.0 kB)
  Using cached docker_pycreds-0.4.0-py2.py3-none-any.whl.metadata (1.8 kB)
  Using cached GitPython-3.1.43-py3-none-any.whl.metadata (13 kB)
  Using cached gitdb-4.0.11-py3-none-any.whl.metadata (1.2 kB)
  Using cached smmap-5.0.1-py3-none-any.whl.metadata (4.3 kB)
   ---------------------------------------- 0.0/6.5 MB ? eta -:--:--
   ---------------------------------------- 0.0/6.5 MB 1.9 MB/s eta 0:00:04
   -- ------------------------------------- 0.4/6.5 MB 5.7 MB/s eta 0:00:02
   ----- ---------------------------------- 0.9/6.5 MB 8.2 MB/s eta 0:00:01
   ---------- ----------------------------- 1.7/6.5 MB 10.8 MB/s eta 0:00:01
   ----------------- ---------------------- 2.9/6.5 MB 14.1 MB/s eta 0:00:01
   ---------------------------- ----------- 4.6/6.5 MB 19.4 MB/s eta 0:00:01
   ---------------------------------------  6.5/6.5 MB 23.0 MB/s eta 0:00:01
   ---------------------------------------  6.5/6.5 MB 23.0 MB/s et

In [11]:
import wandb
import random

# start a new wandb run to track this script
wandb.init(
    # set the wandb project where this run will be logged
    project="my-awesome-project",

    # track hyperparameters and run metadata
    config={
    "learning_rate": 0.02,
    "architecture": "CNN",
    "dataset": "CIFAR-100",
    "epochs": 10,
    }
)

# simulate training
epochs = 10
offset = random.random() / 5
for epoch in range(2, epochs):
    acc = 1 - 2 ** -epoch - random.random() / epoch - offset
    loss = 2 ** -epoch + random.random() / epoch + offset

    # log metrics to wandb
    wandb.log({"acc": acc, "loss": loss})

# [optional] finish the wandb run, necessary in notebooks
wandb.finish()

wandb: Currently logged in as: devanshishah0510 (devanshishah0510-university-of-sussex). Use `wandb login --relogin` to force relogin


## Check scores on VAL data 

In [12]:
# Load your trained model
model = YOLO("C:/Users/ds678/OneDrive - University of Sussex/SAF_Project/runs/segment/train46222/weights/best.pt")

# Run inference on validation dataset
results = model.val(data="C:/Users/ds678/OneDrive - University of Sussex/SAF_Project/Instance_seg_labels/custom_data_PC - Copy.yaml")

Ultralytics YOLOv8.2.75  Python-3.10.14 torch-2.4.0+cu121 CUDA:0 (NVIDIA RTX A4000, 16376MiB)
YOLOv8n-seg summary (fused): 195 layers, 3,258,844 parameters, 0 gradients, 12.0 GFLOPs


val: Scanning C:\Users\ds678\Downloads\Instance_seg_labels\output_updated_last_time\val\labels.cache... 11 images, 0 backgrounds, 0 corrupt: 100%|██████████| 11/11 [00:00<?, ?it/s]Scanning C:\Users\ds678\Downloads\Instance_seg_labels\output_updated_last_time\val\labels.cache... 11 images, 0 backgrounds, 0 corrupt: 100%|██████████| 11/11 [00:00<?, ?it/s]
                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95)     Mask(P          R      mAP50  mAP50-95): 100%|██████████| 1/1 [00:07<00:00,  7.41s/it]


                   all         11        225      0.596      0.492      0.568      0.403      0.449      0.422      0.428      0.233
  ClassicalEvaporation          7        105      0.705      0.433      0.568       0.43       0.46      0.285      0.312     0.0806
    TransitionalMixing          8         61      0.713      0.407      0.579       0.46      0.604      0.351      0.388      0.108
       DiffusiveMixing          6         55      0.398      0.127      0.231      0.139       0.17     0.0545      0.117     0.0366
                 Spray          4          4      0.568          1      0.895      0.583      0.562          1      0.895      0.705
Speed: 0.9ms preprocess, 8.0ms inference, 0.1ms loss, 1.9ms postprocess per image
Results saved to C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\runs\segment\val


# Prediction 

In [23]:
# Load your trained model
model = YOLO("C:/Users/ds678/OneDrive - University of Sussex/SAF_Project/runs/segment/train46222/weights/best.pt")

# Set the input directory and output directory
input_dir = "C:/Users/ds678/OneDrive - University of Sussex/SAF_Project/Instance_seg_labels/output__SAF2022/val/images"
output_dir = "C:/Users/ds678/OneDrive - University of Sussex/SAF_Project/prediction_results"

# Create output directory if it doesn't exist
os.makedirs(output_dir, exist_ok=True)

# Prediction on all images
results = model.predict(input_dir, 
                        save=False,  # We'll save manually
                        conf=0.5, 
                        retina_masks=True, 
                        show_boxes=False)

# Color map for different classes
color_map = {
    'ClassicalEvaporation': (0, 0, 255),  # Blue
    'TransitionalMixing': (0, 255, 255),  # Cyan
    'DiffusiveMixing': (255, 0, 255),  # Magenta
    'Spray': (255, 255, 0)  # Yellow
}

# Process each result
for i, result in enumerate(results):
    # Get the original image
    img = Image.open(result.path).convert("RGB")
    draw = ImageDraw.Draw(img)
    
    # Try to load a font (you might need to adjust the path)
    try:
        font = ImageFont.truetype("arial.ttf", 15)
    except IOError:
        font = ImageFont.load_default()

    # Get predictions
    masks = result.masks.data.cpu().numpy()
    cls = result.boxes.cls.cpu().numpy()
    confs = result.boxes.conf.cpu().numpy()
    
    # Create a new image for the masks
    mask_img = Image.new('RGBA', img.size, (0, 0, 0, 0))
    mask_draw = ImageDraw.Draw(mask_img)

    # Draw masks and labels on the image
    for mask, cl, conf in zip(masks, cls, confs):
        class_name = model.names[int(cl)]
        color = color_map.get(class_name, (255, 255, 255))  # Default to white if class not in color_map
        
        # Convert mask to PIL Image
        mask_image = Image.fromarray((mask * 255).astype(np.uint8))
        
        # Draw the mask
        mask_draw.bitmap((0, 0), mask_image, fill=color + (100,))  # 100 is for semi-transparency

        # Find a point to place the label (e.g., top-left point of the mask)
        non_zero = np.nonzero(mask)
        if len(non_zero[0]) > 0 and len(non_zero[1]) > 0:
            y, x = non_zero[0][0], non_zero[1][0]
            label = f"{class_name} {conf:.2f}"
            draw.text((x, y - 20), label, fill=color, font=font)

    # Combine the original image with the mask
    img = Image.alpha_composite(img.convert('RGBA'), mask_img)

    # Save the image with masks and labels
    img_filename = os.path.basename(result.path)
    img.save(os.path.join(output_dir, f"pred_{img_filename}"))

    # Save labels in YOLO format
    label_filename = os.path.splitext(img_filename)[0] + ".txt"
    with open(os.path.join(output_dir, label_filename), "w") as f:
        for mask, cl, conf in zip(masks, cls, confs):
            # Convert mask to YOLO polygon format
            contours = cv2.findContours((mask > 0.5).astype(np.uint8), cv2.RETR_EXTERNAL, cv2.CHAIN_APPROX_SIMPLE)
            contours = contours[0] if len(contours) == 2 else contours[1]
            if contours:
                # Take the largest contour
                contour = max(contours, key=cv2.contourArea)
                # Simplify the contour
                epsilon = 0.005 * cv2.arcLength(contour, True)
                approx = cv2.approxPolyDP(contour, epsilon, True)
                # Convert to YOLO format
                yolo_polygon = approx.flatten() / np.array([img.width, img.height] * (len(approx.flatten())//2))
                # Write to file: class x1 y1 x2 y2 ... xn yn
                f.write(f"{int(cl)} {' '.join(map(str, yolo_polygon))} {conf}\n")

print(f"Results saved to {output_dir}")


image 1/11 C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\Instance_seg_labels\output__SAF2022\val\images\ABCCWS001_frame_14.png: 768x1024 2 Sprays, 6.0ms
image 2/11 C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\Instance_seg_labels\output__SAF2022\val\images\ABCCWS001_frame_23.png: 768x1024 5 ClassicalEvaporations, 14 TransitionalMixings, 1 DiffusiveMixing, 5.3ms
image 3/11 C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\Instance_seg_labels\output__SAF2022\val\images\ABTCWS004_frame_20.png: 768x1024 6 ClassicalEvaporations, 16 TransitionalMixings, 18 DiffusiveMixings, 5.0ms
image 4/11 C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\Instance_seg_labels\output__SAF2022\val\images\ABTCWS004_frame_24.png: 768x1024 2 ClassicalEvaporations, 6 TransitionalMixings, 6 DiffusiveMixings, 4.0ms
image 5/11 C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\Instance_seg_labels\output__SAF2022\val\images\FBXCWS001_frame_14.png: 768x1024 1 Spray, 

In [22]:
!pip install opencv-python

# YOLOv8m (Medium)

In [4]:
from ultralytics import YOLO

In [5]:
# Train YOLOv8n for segmentation
model = YOLO("yolov8m-seg.yaml")  # build a new model from YAML
model = YOLO("yolov8m-seg.pt")  # load a pretrained model (recommended for training)
model = YOLO("yolov8m-seg.yaml").load("yolov8m-seg.pt")  # build from YAML and transfer weights

Transferred 537/537 items from pretrained weights


# 100 Epochs

In [3]:
# Train the model on custom dataset
results=model.train(data="C:/Users/ds678/OneDrive - University of Sussex/SAF_Project/Instance_seg_labels/custom_data_PC - Copy.yaml", imgsz=1536, epochs=100, task='segment',batch=1, device=0)  # Adjust the path and parameters as needed

New https://pypi.org/project/ultralytics/8.2.79 available  Update with 'pip install -U ultralytics'
Ultralytics YOLOv8.2.75  Python-3.10.14 torch-2.4.0+cu121 CUDA:0 (NVIDIA RTX A4000, 16376MiB)
engine\trainer: task=segment, mode=train, model=yolov8m-seg.yaml, data=C:/Users/ds678/OneDrive - University of Sussex/SAF_Project/Instance_seg_labels/custom_data_PC - Copy.yaml, epochs=100, time=None, patience=100, batch=1, imgsz=1536, save=True, save_period=-1, cache=False, device=0, workers=8, project=None, name=train4, exist_ok=False, pretrained=True, optimizer=auto, verbose=True, seed=0, deterministic=True, single_cls=False, rect=False, cos_lr=False, close_mosaic=10, resume=False, amp=True, fraction=1.0, profile=False, freeze=None, multi_scale=False, overlap_mask=True, mask_ratio=4, dropout=0.0, val=True, split=val, save_json=False, save_hybrid=False, conf=None, iou=0.7, max_det=300, half=False, dnn=False, plots=True, source=None, vid_stride=1, stream_buffer=False, visualize=False, augment=F

wandb: Currently logged in as: devanshishah0510 (devanshishah0510-university-of-sussex). Use `wandb login --relogin` to force relogin


Freezing layer 'model.22.dfl.conv.weight'
AMP: running Automatic Mixed Precision (AMP) checks with YOLOv8n...
AMP: checks passed 


C:\ProgramData\anaconda3\envs\instance\lib\site-packages\ultralytics\engine\trainer.py:269: FutureWarning: `torch.cuda.amp.GradScaler(args...)` is deprecated. Please use `torch.amp.GradScaler('cuda', args...)` instead.
  self.scaler = torch.cuda.amp.GradScaler(enabled=self.amp)
train: Scanning C:\Users\ds678\Downloads\Instance_seg_labels\output_updated_last_time\train\labels.cache... 42 images, 0 backgrounds, 0 corrupt: 100%|██████████| 42/42 [00:00<?, ?it/s]Scanning C:\Users\ds678\Downloads\Instance_seg_labels\output_updated_last_time\train\labels.cache... 42 images, 0 backgrounds, 0 corrupt: 100%|██████████| 42/42 [00:00<?, ?it/s]
val: Scanning C:\Users\ds678\Downloads\Instance_seg_labels\output_updated_last_time\val\labels.cache... 11 images, 0 backgrounds, 0 corrupt: 100%|██████████| 11/11 [00:00<?, ?it/s]Scanning C:\Users\ds678\Downloads\Instance_seg_labels\output_updated_last_time\val\labels.cache... 11 images, 0 backgrounds, 0 corrupt: 100%|██████████| 11/11 [00:00<?, ?it/s]


Plotting labels to C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\runs\segment\train4\labels.jpg... 
optimizer: 'optimizer=auto' found, ignoring 'lr0=0.01' and 'momentum=0.937' and determining best 'optimizer', 'lr0' and 'momentum' automatically... 
optimizer: AdamW(lr=0.00125, momentum=0.9) with parameter groups 86 weight(decay=0.0), 97 weight(decay=0.0005), 96 bias(decay=0.0)
Image sizes 1536 train, 1536 val
Using 8 dataloader workers
Logging results to C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\runs\segment\train4
Starting training for 100 epochs...

      Epoch    GPU_mem   box_loss   seg_loss   cls_loss   dfl_loss  Instances       Size


...

                   all         11        225      0.252       0.59      0.312      0.162      0.184      0.523       0.31      0.124

      Epoch    GPU_mem   box_loss   seg_loss   cls_loss   dfl_loss  Instances       Size


    100/100      3.81G       1.61      1.158      1.845     0.9988         83       1536: 100%|██████████| 42/42 [00:08<00:00,  5.06it/s]
                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95)     Mask(P          R      mAP50  mAP50-95): 100%|██████████| 6/6 [00:00<00:00,  7.72it/s]


                   all         11        225      0.244      0.601      0.316      0.157       0.17       0.51      0.282      0.121

100 epochs completed in 0.282 hours.
Optimizer stripped from C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\runs\segment\train4\weights\last.pt, 55.0MB
Optimizer stripped from C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\runs\segment\train4\weights\best.pt, 55.0MB

Validating C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\runs\segment\train4\weights\best.pt...
Ultralytics YOLOv8.2.75  Python-3.10.14 torch-2.4.0+cu121 CUDA:0 (NVIDIA RTX A4000, 16376MiB)
YOLOv8m-seg summary (fused): 245 layers, 27,224,700 parameters, 0 gradients, 110.0 GFLOPs


                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95)     Mask(P          R      mAP50  mAP50-95): 100%|██████████| 6/6 [00:00<00:00,  8.42it/s]


                   all         11        225      0.225      0.494      0.402      0.155      0.184      0.464      0.359       0.15
  ClassicalEvaporation          7        105      0.337      0.476      0.342      0.181      0.234      0.324      0.218     0.0771
    TransitionalMixing          8         61      0.358      0.721      0.453      0.213      0.257      0.515      0.322      0.124
       DiffusiveMixing          6         55     0.0488     0.0272     0.0483     0.0155     0.0335     0.0182     0.0395     0.0142
                 Spray          4          4      0.155       0.75      0.766       0.21      0.212          1      0.856      0.386
Speed: 2.6ms preprocess, 36.0ms inference, 0.1ms loss, 2.3ms postprocess per image
Results saved to C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\runs\segment\train4


## 500 Epochs

In [4]:
results = model.train(data="C:/Users/ds678/OneDrive - University of Sussex/SAF_Project/Instance_seg_labels/custom_data_PC - Copy.yaml", 
                      imgsz=1536, 
                      epochs=500, 
                      task='segment',
                      batch=1, 
                      device=0,
                      patience=0)

New https://pypi.org/project/ultralytics/8.2.79 available  Update with 'pip install -U ultralytics'
Ultralytics YOLOv8.2.75  Python-3.10.14 torch-2.4.0+cu121 CUDA:0 (NVIDIA RTX A4000, 16376MiB)
engine\trainer: task=segment, mode=train, model=yolov8m-seg.yaml, data=C:/Users/ds678/OneDrive - University of Sussex/SAF_Project/Instance_seg_labels/custom_data_PC - Copy.yaml, epochs=500, time=None, patience=0, batch=1, imgsz=1536, save=True, save_period=-1, cache=False, device=0, workers=8, project=None, name=train42, exist_ok=False, pretrained=True, optimizer=auto, verbose=True, seed=0, deterministic=True, single_cls=False, rect=False, cos_lr=False, close_mosaic=10, resume=False, amp=True, fraction=1.0, profile=False, freeze=None, multi_scale=False, overlap_mask=True, mask_ratio=4, dropout=0.0, val=True, split=val, save_json=False, save_hybrid=False, conf=None, iou=0.7, max_det=300, half=False, dnn=False, plots=True, source=None, vid_stride=1, stream_buffer=False, visualize=False, augment=Fa

Freezing layer 'model.22.dfl.conv.weight'
AMP: running Automatic Mixed Precision (AMP) checks with YOLOv8n...
AMP: checks passed 


train: Scanning C:\Users\ds678\Downloads\Instance_seg_labels\output_updated_last_time\train\labels.cache... 42 images, 0 backgrounds, 0 corrupt: 100%|██████████| 42/42 [00:00<?, ?it/s]Scanning C:\Users\ds678\Downloads\Instance_seg_labels\output_updated_last_time\train\labels.cache... 42 images, 0 backgrounds, 0 corrupt: 100%|██████████| 42/42 [00:00<?, ?it/s]
val: Scanning C:\Users\ds678\Downloads\Instance_seg_labels\output_updated_last_time\val\labels.cache... 11 images, 0 backgrounds, 0 corrupt: 100%|██████████| 11/11 [00:00<?, ?it/s]Scanning C:\Users\ds678\Downloads\Instance_seg_labels\output_updated_last_time\val\labels.cache... 11 images, 0 backgrounds, 0 corrupt: 100%|██████████| 11/11 [00:00<?, ?it/s]


Plotting labels to C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\runs\segment\train42\labels.jpg... 
optimizer: 'optimizer=auto' found, ignoring 'lr0=0.01' and 'momentum=0.937' and determining best 'optimizer', 'lr0' and 'momentum' automatically... 
optimizer: AdamW(lr=0.00125, momentum=0.9) with parameter groups 86 weight(decay=0.0), 97 weight(decay=0.0005), 96 bias(decay=0.0)
Image sizes 1536 train, 1536 val
Using 8 dataloader workers
Logging results to C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\runs\segment\train42
Starting training for 500 epochs...

      Epoch    GPU_mem   box_loss   seg_loss   cls_loss   dfl_loss  Instances       Size


      1/500      4.91G      1.831      1.196      2.046      1.114         41       1536: 100%|██████████| 42/42 [00:48<00:00,  1.15s/it]
                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95)     Mask(P          R      mAP50  mAP50-95): 100%|██████████| 6/6 [00:00<00:00,  9.30it/s]


...

                   all         11        225      0.312      0.395        0.3      0.185      0.259      0.348      0.245      0.106

      Epoch    GPU_mem   box_loss   seg_loss   cls_loss   dfl_loss  Instances       Size


    500/500      3.77G      1.158     0.7092      1.082     0.9036         15       1536: 100%|██████████| 42/42 [00:07<00:00,  5.57it/s]
                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95)     Mask(P          R      mAP50  mAP50-95): 100%|██████████| 6/6 [00:00<00:00, 11.59it/s]


                   all         11        225      0.302      0.389      0.296      0.191      0.252      0.344      0.258      0.116

500 epochs completed in 1.369 hours.
Optimizer stripped from C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\runs\segment\train42\weights\last.pt, 55.1MB
Optimizer stripped from C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\runs\segment\train42\weights\best.pt, 55.0MB

Validating C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\runs\segment\train42\weights\best.pt...
Ultralytics YOLOv8.2.75  Python-3.10.14 torch-2.4.0+cu121 CUDA:0 (NVIDIA RTX A4000, 16376MiB)
YOLOv8m-seg summary (fused): 245 layers, 27,224,700 parameters, 0 gradients, 110.0 GFLOPs


                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95)     Mask(P          R      mAP50  mAP50-95): 100%|██████████| 6/6 [00:00<00:00,  8.51it/s]


                   all         11        225      0.339       0.54      0.395      0.208      0.332      0.492      0.386      0.179
  ClassicalEvaporation          7        105      0.521      0.371       0.47      0.272      0.454      0.267      0.297     0.0991
    TransitionalMixing          8         61      0.439      0.623      0.434      0.253      0.435      0.555      0.382      0.166
       DiffusiveMixing          6         55       0.19      0.164      0.148     0.0538      0.229      0.146      0.129     0.0581
                 Spray          4          4      0.206          1       0.53      0.253      0.211          1      0.736      0.395
Speed: 2.6ms preprocess, 37.0ms inference, 0.0ms loss, 3.1ms postprocess per image
Results saved to C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\runs\segment\train42


# 1000 Epochs

In [5]:
results = model.train(data="C:/Users/ds678/OneDrive - University of Sussex/SAF_Project/Instance_seg_labels/custom_data_PC - Copy.yaml", 
                      imgsz=1536, 
                      epochs=1000, 
                      task='segment',
                      batch=1, 
                      device=0,
                      patience=0)

New https://pypi.org/project/ultralytics/8.2.79 available  Update with 'pip install -U ultralytics'
Ultralytics YOLOv8.2.75  Python-3.10.14 torch-2.4.0+cu121 CUDA:0 (NVIDIA RTX A4000, 16376MiB)
engine\trainer: task=segment, mode=train, model=yolov8m-seg.yaml, data=C:/Users/ds678/OneDrive - University of Sussex/SAF_Project/Instance_seg_labels/custom_data_PC - Copy.yaml, epochs=1000, time=None, patience=0, batch=1, imgsz=1536, save=True, save_period=-1, cache=False, device=0, workers=8, project=None, name=train422, exist_ok=False, pretrained=True, optimizer=auto, verbose=True, seed=0, deterministic=True, single_cls=False, rect=False, cos_lr=False, close_mosaic=10, resume=False, amp=True, fraction=1.0, profile=False, freeze=None, multi_scale=False, overlap_mask=True, mask_ratio=4, dropout=0.0, val=True, split=val, save_json=False, save_hybrid=False, conf=None, iou=0.7, max_det=300, half=False, dnn=False, plots=True, source=None, vid_stride=1, stream_buffer=False, visualize=False, augment=

Freezing layer 'model.22.dfl.conv.weight'
AMP: running Automatic Mixed Precision (AMP) checks with YOLOv8n...
AMP: checks passed 


train: Scanning C:\Users\ds678\Downloads\Instance_seg_labels\output_updated_last_time\train\labels.cache... 42 images, 0 backgrounds, 0 corrupt: 100%|██████████| 42/42 [00:00<?, ?it/s]Scanning C:\Users\ds678\Downloads\Instance_seg_labels\output_updated_last_time\train\labels.cache... 42 images, 0 backgrounds, 0 corrupt: 100%|██████████| 42/42 [00:00<?, ?it/s]
val: Scanning C:\Users\ds678\Downloads\Instance_seg_labels\output_updated_last_time\val\labels.cache... 11 images, 0 backgrounds, 0 corrupt: 100%|██████████| 11/11 [00:00<?, ?it/s]Scanning C:\Users\ds678\Downloads\Instance_seg_labels\output_updated_last_time\val\labels.cache... 11 images, 0 backgrounds, 0 corrupt: 100%|██████████| 11/11 [00:00<?, ?it/s]


Plotting labels to C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\runs\segment\train422\labels.jpg... 
optimizer: 'optimizer=auto' found, ignoring 'lr0=0.01' and 'momentum=0.937' and determining best 'optimizer', 'lr0' and 'momentum' automatically... 
optimizer: AdamW(lr=0.00125, momentum=0.9) with parameter groups 86 weight(decay=0.0), 97 weight(decay=0.0005), 96 bias(decay=0.0)
Image sizes 1536 train, 1536 val
Using 8 dataloader workers
Logging results to C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\runs\segment\train422
Starting training for 1000 epochs...

      Epoch    GPU_mem   box_loss   seg_loss   cls_loss   dfl_loss  Instances       Size


     1/1000      5.07G      1.564      1.004       1.58      1.033         41       1536: 100%|██████████| 42/42 [00:07<00:00,  5.47it/s]
                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95)     Mask(P          R      mAP50  mAP50-95): 100%|██████████| 6/6 [00:00<00:00,  8.14it/s]


...

                   all         11        225      0.364       0.37      0.356      0.227      0.299      0.351      0.263      0.131

      Epoch    GPU_mem   box_loss   seg_loss   cls_loss   dfl_loss  Instances       Size


  1000/1000      4.13G      1.026     0.6981     0.7607     0.8348         15       1536: 100%|██████████| 42/42 [00:07<00:00,  5.27it/s]
                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95)     Mask(P          R      mAP50  mAP50-95): 100%|██████████| 6/6 [00:00<00:00,  8.59it/s]


                   all         11        225      0.355      0.364      0.359      0.225      0.299      0.338      0.263      0.127

1000 epochs completed in 2.731 hours.
Optimizer stripped from C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\runs\segment\train422\weights\last.pt, 55.2MB
Optimizer stripped from C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\runs\segment\train422\weights\best.pt, 55.1MB

Validating C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\runs\segment\train422\weights\best.pt...
Ultralytics YOLOv8.2.75  Python-3.10.14 torch-2.4.0+cu121 CUDA:0 (NVIDIA RTX A4000, 16376MiB)
YOLOv8m-seg summary (fused): 245 layers, 27,224,700 parameters, 0 gradients, 110.0 GFLOPs


                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95)     Mask(P          R      mAP50  mAP50-95): 100%|██████████| 6/6 [00:00<00:00,  8.24it/s]


                   all         11        225      0.366       0.45      0.439      0.235      0.346      0.346      0.348      0.159
  ClassicalEvaporation          7        105      0.651      0.533      0.663      0.374      0.558      0.337      0.425      0.171
    TransitionalMixing          8         61      0.455      0.689      0.557      0.376      0.467       0.56      0.488      0.243
       DiffusiveMixing          6         55      0.343      0.327       0.29      0.142      0.345      0.236      0.233      0.122
                 Spray          4          4     0.0118       0.25      0.247     0.0493      0.012       0.25      0.247     0.0987
Speed: 2.2ms preprocess, 36.4ms inference, 0.0ms loss, 2.4ms postprocess per image
Results saved to C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\runs\segment\train422


# 3000 Epochs

In [6]:
results = model.train(data="C:/Users/ds678/OneDrive - University of Sussex/SAF_Project/Instance_seg_labels/custom_data_PC - Copy.yaml", 
                      imgsz=1536, 
                      epochs=3000, 
                      task='segment',
                      batch=1, 
                      device=0,
                      patience=0)

New https://pypi.org/project/ultralytics/8.2.79 available  Update with 'pip install -U ultralytics'
Ultralytics YOLOv8.2.75  Python-3.10.14 torch-2.4.0+cu121 CUDA:0 (NVIDIA RTX A4000, 16376MiB)
engine\trainer: task=segment, mode=train, model=yolov8m-seg.yaml, data=C:/Users/ds678/OneDrive - University of Sussex/SAF_Project/Instance_seg_labels/custom_data_PC - Copy.yaml, epochs=3000, time=None, patience=0, batch=1, imgsz=1536, save=True, save_period=-1, cache=False, device=0, workers=8, project=None, name=train4222, exist_ok=False, pretrained=True, optimizer=auto, verbose=True, seed=0, deterministic=True, single_cls=False, rect=False, cos_lr=False, close_mosaic=10, resume=False, amp=True, fraction=1.0, profile=False, freeze=None, multi_scale=False, overlap_mask=True, mask_ratio=4, dropout=0.0, val=True, split=val, save_json=False, save_hybrid=False, conf=None, iou=0.7, max_det=300, half=False, dnn=False, plots=True, source=None, vid_stride=1, stream_buffer=False, visualize=False, augment

Freezing layer 'model.22.dfl.conv.weight'
AMP: running Automatic Mixed Precision (AMP) checks with YOLOv8n...
AMP: checks passed 


train: Scanning C:\Users\ds678\Downloads\Instance_seg_labels\output_updated_last_time\train\labels.cache... 42 images, 0 backgrounds, 0 corrupt: 100%|██████████| 42/42 [00:00<?, ?it/s]Scanning C:\Users\ds678\Downloads\Instance_seg_labels\output_updated_last_time\train\labels.cache... 42 images, 0 backgrounds, 0 corrupt: 100%|██████████| 42/42 [00:00<?, ?it/s]
val: Scanning C:\Users\ds678\Downloads\Instance_seg_labels\output_updated_last_time\val\labels.cache... 11 images, 0 backgrounds, 0 corrupt: 100%|██████████| 11/11 [00:00<?, ?it/s]Scanning C:\Users\ds678\Downloads\Instance_seg_labels\output_updated_last_time\val\labels.cache... 11 images, 0 backgrounds, 0 corrupt: 100%|██████████| 11/11 [00:00<?, ?it/s]


Plotting labels to C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\runs\segment\train4222\labels.jpg... 
optimizer: 'optimizer=auto' found, ignoring 'lr0=0.01' and 'momentum=0.937' and determining best 'optimizer', 'lr0' and 'momentum' automatically... 
optimizer: AdamW(lr=0.00125, momentum=0.9) with parameter groups 86 weight(decay=0.0), 97 weight(decay=0.0005), 96 bias(decay=0.0)
Image sizes 1536 train, 1536 val
Using 8 dataloader workers
Logging results to C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\runs\segment\train4222
Starting training for 3000 epochs...

      Epoch    GPU_mem   box_loss   seg_loss   cls_loss   dfl_loss  Instances       Size


     1/3000      4.89G      1.027     0.5442     0.9032     0.9223         41       1536: 100%|██████████| 42/42 [00:08<00:00,  5.08it/s]
                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95)     Mask(P          R      mAP50  mAP50-95): 100%|██████████| 6/6 [00:00<00:00,  8.85it/s]


...

                   all         11        225      0.368      0.615      0.396      0.242      0.297      0.529      0.313      0.151

      Epoch    GPU_mem   box_loss   seg_loss   cls_loss   dfl_loss  Instances       Size


  3000/3000      4.06G     0.7994     0.7538     0.4058     0.7869         20       1536: 100%|██████████| 42/42 [00:20<00:00,  2.00it/s]
                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95)     Mask(P          R      mAP50  mAP50-95): 100%|██████████| 6/6 [00:02<00:00,  2.10it/s]


                   all         11        225      0.368      0.615      0.396      0.242      0.297      0.529      0.313      0.151

3000 epochs completed in 12.931 hours.
Optimizer stripped from C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\runs\segment\train4222\weights\last.pt, 55.5MB
Optimizer stripped from C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\runs\segment\train4222\weights\best.pt, 55.3MB

Validating C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\runs\segment\train4222\weights\best.pt...
Ultralytics YOLOv8.2.75  Python-3.10.14 torch-2.4.0+cu121 CUDA:0 (NVIDIA RTX A4000, 16376MiB)
YOLOv8m-seg summary (fused): 245 layers, 27,224,700 parameters, 0 gradients, 110.0 GFLOPs


                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95)     Mask(P          R      mAP50  mAP50-95): 100%|██████████| 6/6 [00:01<00:00,  3.69it/s]


                   all         11        225      0.466      0.557      0.576      0.311      0.408      0.456      0.475      0.214
  ClassicalEvaporation          7        105      0.755      0.559      0.685      0.399      0.608      0.362      0.429      0.196
    TransitionalMixing          8         61      0.594      0.574      0.624      0.428      0.581      0.475      0.567      0.296
       DiffusiveMixing          6         55      0.422      0.345      0.366      0.186       0.35      0.236      0.251      0.119
                 Spray          4          4     0.0925       0.75      0.627       0.23     0.0952       0.75      0.652      0.244
Speed: 4.0ms preprocess, 65.0ms inference, 0.0ms loss, 12.3ms postprocess per image
Results saved to C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\runs\segment\train4222


In [7]:
import wandb
import random

# start a new wandb run to track this script
wandb.init(
    # set the wandb project where this run will be logged
    project="my-awesome-project",

    # track hyperparameters and run metadata
    config={
    "learning_rate": 0.02,
    "architecture": "CNN",
    "dataset": "CIFAR-100",
    "epochs": 10,
    }
)

# simulate training
epochs = 10
offset = random.random() / 5
for epoch in range(2, epochs):
    acc = 1 - 2 ** -epoch - random.random() / epoch - offset
    loss = 2 ** -epoch + random.random() / epoch + offset

    # log metrics to wandb
    wandb.log({"acc": acc, "loss": loss})

# [optional] finish the wandb run, necessary in notebooks
wandb.finish()

## Check scores on VAL data

In [8]:
# Load your trained model
model = YOLO("C:/Users/ds678/OneDrive - University of Sussex/SAF_Project/runs/segment/train4222/weights/best.pt")

# Run inference on validation dataset
results = model.val(data="C:/Users/ds678/OneDrive - University of Sussex/SAF_Project/Instance_seg_labels/custom_data_PC - Copy.yaml")

Ultralytics YOLOv8.2.75  Python-3.10.14 torch-2.4.0+cu121 CUDA:0 (NVIDIA RTX A4000, 16376MiB)
YOLOv8m-seg summary (fused): 245 layers, 27,224,700 parameters, 0 gradients, 110.0 GFLOPs


val: Scanning C:\Users\ds678\Downloads\Instance_seg_labels\output_updated_last_time\val\labels.cache... 11 images, 0 backgrounds, 0 corrupt: 100%|██████████| 11/11 [00:00<?, ?it/s]Scanning C:\Users\ds678\Downloads\Instance_seg_labels\output_updated_last_time\val\labels.cache... 11 images, 0 backgrounds, 0 corrupt: 100%|██████████| 11/11 [00:00<?, ?it/s]
                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95)     Mask(P          R      mAP50  mAP50-95): 100%|██████████| 1/1 [00:15<00:00, 15.33s/it]


                   all         11        225      0.468      0.557       0.48      0.304      0.425      0.428      0.354      0.155
  ClassicalEvaporation          7        105      0.755      0.558       0.68      0.429      0.567      0.295      0.384      0.136
    TransitionalMixing          8         61      0.594      0.574      0.624      0.462      0.599      0.465      0.549      0.228
       DiffusiveMixing          6         55      0.425      0.345      0.372      0.202      0.428        0.2      0.237      0.099
                 Spray          4          4     0.0975       0.75      0.245      0.126      0.105       0.75      0.245      0.157
Speed: 9.8ms preprocess, 736.9ms inference, 0.0ms loss, 1.3ms postprocess per image
Results saved to C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\runs\segment\val4


## Prediction

In [9]:
from ultralytics import YOLO
from PIL import Image, ImageDraw, ImageFont
import numpy as np
import os
import cv2  

# Load your trained model
model = YOLO("C:/Users/ds678/OneDrive - University of Sussex/SAF_Project/runs/segment/train46222/weights/best.pt")

# Set the input directory and output directory
input_dir = "C:/Users/ds678/OneDrive - University of Sussex/SAF_Project/Instance_seg_labels/output__SAF2022/val/images"
output_dir = "C:/Users/ds678/OneDrive - University of Sussex/SAF_Project/prediction_results"

# Create output directory if it doesn't exist
os.makedirs(output_dir, exist_ok=True)

# Prediction on all images
results = model.predict(input_dir, 
                        save=False,  # We'll save manually
                        conf=0.5, 
                        retina_masks=True, 
                        show_boxes=False)

# Color map for different classes
color_map = {
    'ClassicalEvaporation': (0, 0, 255),  # Blue
    'TransitionalMixing': (0, 255, 255),  # Cyan
    'DiffusiveMixing': (255, 0, 255),  # Magenta
    'Spray': (255, 255, 0)  # Yellow
}

# Process each result
for i, result in enumerate(results):
    # Get the original image
    img = Image.open(result.path).convert("RGB")
    draw = ImageDraw.Draw(img)
    
    # Try to load a font (you might need to adjust the path)
    try:
        font = ImageFont.truetype("arial.ttf", 15)
    except IOError:
        font = ImageFont.load_default()

    # Get predictions
    masks = result.masks.data.cpu().numpy()
    cls = result.boxes.cls.cpu().numpy()
    confs = result.boxes.conf.cpu().numpy()
    
    # Create a new image for the masks
    mask_img = Image.new('RGBA', img.size, (0, 0, 0, 0))
    mask_draw = ImageDraw.Draw(mask_img)

    # Draw masks and labels on the image
    for mask, cl, conf in zip(masks, cls, confs):
        class_name = model.names[int(cl)]
        color = color_map.get(class_name, (255, 255, 255))  # Default to white if class not in color_map
        
        # Convert mask to PIL Image
        mask_image = Image.fromarray((mask * 255).astype(np.uint8))
        
        # Draw the mask
        mask_draw.bitmap((0, 0), mask_image, fill=color + (100,))  # 100 is for semi-transparency

        # Find a point to place the label (e.g., top-left point of the mask)
        non_zero = np.nonzero(mask)
        if len(non_zero[0]) > 0 and len(non_zero[1]) > 0:
            y, x = non_zero[0][0], non_zero[1][0]
            label = f"{class_name} {conf:.2f}"
            draw.text((x, y - 20), label, fill=color, font=font)

    # Combine the original image with the mask
    img = Image.alpha_composite(img.convert('RGBA'), mask_img)

    # Save the image with masks and labels
    img_filename = os.path.basename(result.path)
    img.save(os.path.join(output_dir, f"pred_{img_filename}"))

    # Save labels in YOLO format
    label_filename = os.path.splitext(img_filename)[0] + ".txt"
    with open(os.path.join(output_dir, label_filename), "w") as f:
        for mask, cl, conf in zip(masks, cls, confs):
            # Convert mask to YOLO polygon format
            contours = cv2.findContours((mask > 0.5).astype(np.uint8), cv2.RETR_EXTERNAL, cv2.CHAIN_APPROX_SIMPLE)
            contours = contours[0] if len(contours) == 2 else contours[1]
            if contours:
                # Take the largest contour
                contour = max(contours, key=cv2.contourArea)
                # Simplify the contour
                epsilon = 0.005 * cv2.arcLength(contour, True)
                approx = cv2.approxPolyDP(contour, epsilon, True)
                # Convert to YOLO format
                yolo_polygon = approx.flatten() / np.array([img.width, img.height] * (len(approx.flatten())//2))
                # Write to file: class x1 y1 x2 y2 ... xn yn
                f.write(f"{int(cl)} {' '.join(map(str, yolo_polygon))} {conf}\n")

print(f"Results saved to {output_dir}")


image 1/11 C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\Instance_seg_labels\output__SAF2022\val\images\ABCCWS001_frame_14.png: 1152x1536 10 Sprays, 1053.5ms
image 2/11 C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\Instance_seg_labels\output__SAF2022\val\images\ABCCWS001_frame_23.png: 1152x1536 8 ClassicalEvaporations, 18 TransitionalMixings, 4 DiffusiveMixings, 582.0ms
image 3/11 C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\Instance_seg_labels\output__SAF2022\val\images\ABTCWS004_frame_20.png: 1152x1536 8 ClassicalEvaporations, 19 TransitionalMixings, 26 DiffusiveMixings, 140.5ms
image 4/11 C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\Instance_seg_labels\output__SAF2022\val\images\ABTCWS004_frame_24.png: 1152x1536 1 ClassicalEvaporation, 6 TransitionalMixings, 7 DiffusiveMixings, 139.5ms
image 5/11 C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\Instance_seg_labels\output__SAF2022\val\images\FBXCWS001_frame_14.png: 1152

In [7]:
!pip install torch torchvision torchaudio

## Hypertuning

In [6]:
import os
import torch
import albumentations as A
from albumentations.pytorch import ToTensorV2
from torch.utils.data import Dataset
from ultralytics import YOLO

# Define augmentation transformations
augmentations = A.Compose([
    A.RandomRotate90(p=0.5),
    A.Rotate(limit=30, p=0.5),
    A.RandomScale(scale_limit=0.2, p=0.5),
    A.Resize(1024, 1024),
    A.HorizontalFlip(p=0.5),
    A.VerticalFlip(p=0.5),
    A.RandomBrightnessContrast(p=0.2),
    A.GaussNoise(p=0.2),
    ToTensorV2()
], bbox_params=A.BboxParams(format='yolo', label_fields=['class_labels']))

# Load your YOLO model
model = YOLO("C:/Users/ds678/OneDrive - University of Sussex/SAF_Project/runs/segment/train4222/weights/best.pt")

# Hyperparameter tuning
hyperparameters = {
    'imgsz': 1024,
    'epochs': 500,
    'batch': 1,
    'lr0': [0.001, 0.0001],  # Initial learning rates for tuning
    'momentum': [0.9, 0.95],
    'weight_decay': [0.0005, 0.0001]
}

# Example loop for hyperparameter tuning
counter = 0
for lr in hyperparameters['lr0']:
    for momentum in hyperparameters['momentum']:
        for weight_decay in hyperparameters['weight_decay']:
            if counter < 2:  # Run the loop only 3 times
                print(f"Training with lr0={lr}, momentum={momentum}, weight_decay={weight_decay}")
                
                # Adjusting parameters directly in the `train()` method
                results = model.train(
                    data=("C:/Users/ds678/OneDrive - University of Sussex/SAF_Project/Instance_seg_labels/custom_data_PC - Copy.yaml"),
                    imgsz=hyperparameters['imgsz'],
                    epochs=hyperparameters['epochs'],
                    batch=hyperparameters['batch'],
                    device=0,
                    lr0=lr,
                    momentum=momentum,
                    weight_decay=weight_decay,
                    patience=0,
                )
                
                print("Completed training with lr0={lr}, momentum={momentum}, weight_decay={weight_decay}")
                counter += 1
            else:
                break

Training with lr0=0.001, momentum=0.9, weight_decay=0.0005
New https://pypi.org/project/ultralytics/8.2.79 available  Update with 'pip install -U ultralytics'
Ultralytics YOLOv8.2.75  Python-3.10.14 torch-2.4.0+cu121 CUDA:0 (NVIDIA RTX A4000, 16376MiB)
engine\trainer: task=segment, mode=train, model=C:/Users/ds678/OneDrive - University of Sussex/SAF_Project/runs/segment/train4222/weights/best.pt, data=C:/Users/ds678/OneDrive - University of Sussex/SAF_Project/Instance_seg_labels/custom_data_PC - Copy.yaml, epochs=500, time=None, patience=0, batch=1, imgsz=1024, save=True, save_period=-1, cache=False, device=0, workers=8, project=None, name=train10, exist_ok=False, pretrained=True, optimizer=auto, verbose=True, seed=0, deterministic=True, single_cls=False, rect=False, cos_lr=False, close_mosaic=10, resume=False, amp=True, fraction=1.0, profile=False, freeze=None, multi_scale=False, overlap_mask=True, mask_ratio=4, dropout=0.0, val=True, split=val, save_json=False, save_hybrid=False, con

train: Scanning C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\Instance_seg_labels\output__SAF2022\train\labels.cache... 42 images, 0 backgrounds, 0 corrupt: 100%|██████████| 42/42 [00:00<?, ?it/s]Scanning C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\Instance_seg_labels\output__SAF2022\train\labels.cache... 42 images, 0 backgrounds, 0 corrupt: 100%|██████████| 42/42 [00:00<?, ?it/s]


albumentations: Blur(p=0.01, blur_limit=(3, 7)), MedianBlur(p=0.01, blur_limit=(3, 7)), ToGray(p=0.01), CLAHE(p=0.01, clip_limit=(1, 4.0), tile_grid_size=(8, 8))


val: Scanning C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\Instance_seg_labels\output__SAF2022\val\labels.cache... 11 images, 0 backgrounds, 0 corrupt: 100%|██████████| 11/11 [00:00<?, ?it/s]Scanning C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\Instance_seg_labels\output__SAF2022\val\labels.cache... 11 images, 0 backgrounds, 0 corrupt: 100%|██████████| 11/11 [00:00<?, ?it/s]


Plotting labels to C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\runs\segment\train10\labels.jpg... 
optimizer: 'optimizer=auto' found, ignoring 'lr0=0.001' and 'momentum=0.9' and determining best 'optimizer', 'lr0' and 'momentum' automatically... 
optimizer: AdamW(lr=0.00125, momentum=0.9) with parameter groups 86 weight(decay=0.0), 97 weight(decay=0.0005), 96 bias(decay=0.0)
Image sizes 1024 train, 1024 val
Using 8 dataloader workers
Logging results to C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\runs\segment\train10
Starting training for 500 epochs...

      Epoch    GPU_mem   box_loss   seg_loss   cls_loss   dfl_loss  Instances       Size


...

    500/500      2.46G     0.7848     0.4289     0.4684     0.7896          9       1024: 100%|██████████| 42/42 [00:02<00:00, 14.05it/s]
                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95)     Mask(P          R      mAP50  mAP50-95): 100%|██████████| 6/6 [00:00<00:00, 13.29it/s]


                   all         11        215      0.499      0.583      0.554      0.341      0.386      0.499      0.435       0.16

500 epochs completed in 0.643 hours.
Optimizer stripped from C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\runs\segment\train102\weights\last.pt, 55.0MB
Optimizer stripped from C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\runs\segment\train102\weights\best.pt, 54.9MB

Validating C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\runs\segment\train102\weights\best.pt...
Ultralytics YOLOv8.2.75  Python-3.10.14 torch-2.4.0+cu121 CUDA:0 (NVIDIA RTX A4000, 16376MiB)
YOLOv8m-seg summary (fused): 245 layers, 27,224,700 parameters, 0 gradients, 110.0 GFLOPs


                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95)     Mask(P          R      mAP50  mAP50-95): 100%|██████████| 6/6 [00:00<00:00, 11.23it/s]


                   all         11        215      0.529      0.642      0.563      0.346      0.443      0.557      0.445      0.163
  ClassicalEvaporation          7         52      0.647      0.615      0.671      0.482      0.513      0.481      0.467      0.118
    TransitionalMixing          6         82      0.633       0.59      0.615      0.446       0.51      0.463      0.456      0.156
       DiffusiveMixing          6         77      0.614      0.364      0.472      0.276      0.526      0.286      0.362      0.129
                 Spray          4          4      0.221          1      0.495      0.181      0.222          1      0.495       0.25
Speed: 0.5ms preprocess, 36.3ms inference, 0.1ms loss, 2.3ms postprocess per image
Results saved to C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\runs\segment\train102


Completed training with lr0={lr}, momentum={momentum}, weight_decay={weight_decay}


## Prediction on Hypertuning

In [7]:
from ultralytics import YOLO
from PIL import Image, ImageDraw, ImageFont
import numpy as np
import os
import cv2  

# Load your trained model
model = YOLO("C:/Users/ds678/OneDrive - University of Sussex/SAF_Project/runs/segment/train102/weights/best.pt")

# Set the input directory and output directory
input_dir = "C:/Users/ds678/OneDrive - University of Sussex/SAF_Project/Instance_seg_labels/output__SAF2022/val/images"
output_dir = "C:/Users/ds678/OneDrive - University of Sussex/SAF_Project/Tuned_prediction_results"

# Create output directory if it doesn't exist
os.makedirs(output_dir, exist_ok=True)

# Prediction on all images
results = model.predict(input_dir, 
                        save=False,  # We'll save manually
                        conf=0.5, 
                        retina_masks=True, 
                        show_boxes=False)

# Color map for different classes
color_map = {
    'ClassicalEvaporation': (0, 0, 255),  # Blue
    'TransitionalMixing': (0, 255, 255),  # Cyan
    'DiffusiveMixing': (255, 0, 255),  # Magenta
    'Spray': (255, 255, 0)  # Yellow
}

# Process each result
for i, result in enumerate(results):
    # Get the original image
    img = Image.open(result.path).convert("RGB")
    draw = ImageDraw.Draw(img)
    
    # Try to load a font (you might need to adjust the path)
    try:
        font = ImageFont.truetype("arial.ttf", 15)
    except IOError:
        font = ImageFont.load_default()

    # Get predictions
    masks = result.masks.data.cpu().numpy()
    cls = result.boxes.cls.cpu().numpy()
    confs = result.boxes.conf.cpu().numpy()
    
    # Create a new image for the masks
    mask_img = Image.new('RGBA', img.size, (0, 0, 0, 0))
    mask_draw = ImageDraw.Draw(mask_img)

    # Draw masks and labels on the image
    for mask, cl, conf in zip(masks, cls, confs):
        class_name = model.names[int(cl)]
        color = color_map.get(class_name, (255, 255, 255))  # Default to white if class not in color_map
        
        # Convert mask to PIL Image
        mask_image = Image.fromarray((mask * 255).astype(np.uint8))
        
        # Draw the mask
        mask_draw.bitmap((0, 0), mask_image, fill=color + (100,))  # 100 is for semi-transparency

        # Find a point to place the label (e.g., top-left point of the mask)
        non_zero = np.nonzero(mask)
        if len(non_zero[0]) > 0 and len(non_zero[1]) > 0:
            y, x = non_zero[0][0], non_zero[1][0]
            label = f"{class_name} {conf:.2f}"
            draw.text((x, y - 20), label, fill=color, font=font)

    # Combine the original image with the mask
    img = Image.alpha_composite(img.convert('RGBA'), mask_img)

    # Save the image with masks and labels
    img_filename = os.path.basename(result.path)
    img.save(os.path.join(output_dir, f"pred_{img_filename}"))

    # Save labels in YOLO format
    label_filename = os.path.splitext(img_filename)[0] + ".txt"
    with open(os.path.join(output_dir, label_filename), "w") as f:
        for mask, cl, conf in zip(masks, cls, confs):
            # Convert mask to YOLO polygon format
            contours = cv2.findContours((mask > 0.5).astype(np.uint8), cv2.RETR_EXTERNAL, cv2.CHAIN_APPROX_SIMPLE)
            contours = contours[0] if len(contours) == 2 else contours[1]
            if contours:
                # Take the largest contour
                contour = max(contours, key=cv2.contourArea)
                # Simplify the contour
                epsilon = 0.005 * cv2.arcLength(contour, True)
                approx = cv2.approxPolyDP(contour, epsilon, True)
                # Convert to YOLO format
                yolo_polygon = approx.flatten() / np.array([img.width, img.height] * (len(approx.flatten())//2))
                # Write to file: class x1 y1 x2 y2 ... xn yn
                f.write(f"{int(cl)} {' '.join(map(str, yolo_polygon))} {conf}\n")

print("Results saved to {output_dir}")


image 1/11 C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\Instance_seg_labels\output__SAF2022\val\images\ABCCWS001_frame_14.png: 768x1024 6 Sprays, 45.9ms
image 2/11 C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\Instance_seg_labels\output__SAF2022\val\images\ABCCWS001_frame_23.png: 768x1024 4 ClassicalEvaporations, 9 TransitionalMixings, 1 DiffusiveMixing, 21.9ms
image 3/11 C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\Instance_seg_labels\output__SAF2022\val\images\ABTCWS004_frame_20.png: 768x1024 5 ClassicalEvaporations, 6 TransitionalMixings, 1 DiffusiveMixing, 20.9ms
image 4/11 C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\Instance_seg_labels\output__SAF2022\val\images\ABTCWS004_frame_24.png: 768x1024 1 ClassicalEvaporation, 3 TransitionalMixings, 4 DiffusiveMixings, 19.9ms
image 5/11 C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\Instance_seg_labels\output__SAF2022\val\images\FBXCWS001_frame_14.png: 768x1024 2 Sprays, 

In [8]:
# Load your best trained model
model = YOLO("C:/Users/ds678/OneDrive - University of Sussex/SAF_Project/runs/segment/train102/weights/best.pt")

# Export the model to ONNX format
model.export(format='onnx')

Ultralytics YOLOv8.2.75  Python-3.10.14 torch-2.4.0+cu121 CPU (12th Gen Intel Core(TM) i9-12900)
YOLOv8m-seg summary (fused): 245 layers, 27,224,700 parameters, 0 gradients, 110.0 GFLOPs

PyTorch: starting from 'C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\runs\segment\train102\weights\best.pt' with input shape (1, 3, 1024, 1024) BCHW and output shape(s) ((1, 40, 21504), (1, 32, 256, 256)) (52.4 MB)

ONNX: starting export with onnx 1.16.2 opset 19...
ONNX: export success  4.4s, saved as 'C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\runs\segment\train102\weights\best.onnx' (104.3 MB)

Export complete (14.1s)
Results saved to C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\runs\segment\train102\weights
Predict:         yolo predict task=segment model=C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\runs\segment\train102\weights\best.onnx imgsz=1024  
Validate:        yolo val task=segment model=C:\Users\ds678\OneDrive - University of Susse

'C:\\Users\\ds678\\OneDrive - University of Sussex\\SAF_Project\\runs\\segment\\train102\\weights\\best.onnx'

In [9]:
print("Model exported to ONNX format.")

Model exported to ONNX format.


# YOLOv8l

In [3]:
from ultralytics import YOLO

In [4]:
# Train YOLOv8n for segmentation
model = YOLO("yolov8l-seg.yaml")  # build a new model from YAML
model = YOLO("yolov8l-seg.pt")  # load a pretrained model (recommended for training)
model = YOLO("yolov8l-seg.yaml").load("yolov8l-seg.pt")  # build from YAML and transfer weights

Transferred 657/657 items from pretrained weights


## 100 Epochs

In [12]:
# Train the model on custom dataset
results=model.train(data="C:/Users/ds678/OneDrive - University of Sussex/SAF_Project/Instance_seg_labels/custom_data_PC - Copy.yaml", imgsz=1536, epochs=100, task='segment',batch=1, device=0)  # Adjust the path and parameters as needed

New https://pypi.org/project/ultralytics/8.2.79 available  Update with 'pip install -U ultralytics'
Ultralytics YOLOv8.2.75  Python-3.10.14 torch-2.4.0+cu121 CUDA:0 (NVIDIA RTX A4000, 16376MiB)
engine\trainer: task=segment, mode=train, model=yolov8l-seg.yaml, data=C:/Users/ds678/OneDrive - University of Sussex/SAF_Project/Instance_seg_labels/custom_data_PC - Copy.yaml, epochs=100, time=None, patience=100, batch=1, imgsz=1536, save=True, save_period=-1, cache=False, device=0, workers=8, project=None, name=train6, exist_ok=False, pretrained=True, optimizer=auto, verbose=True, seed=0, deterministic=True, single_cls=False, rect=False, cos_lr=False, close_mosaic=10, resume=False, amp=True, fraction=1.0, profile=False, freeze=None, multi_scale=False, overlap_mask=True, mask_ratio=4, dropout=0.0, val=True, split=val, save_json=False, save_hybrid=False, conf=None, iou=0.7, max_det=300, half=False, dnn=False, plots=True, source=None, vid_stride=1, stream_buffer=False, visualize=False, augment=F

Freezing layer 'model.22.dfl.conv.weight'
AMP: running Automatic Mixed Precision (AMP) checks with YOLOv8n...
AMP: checks passed 


train: Scanning C:\Users\ds678\Downloads\Instance_seg_labels\output_updated_last_time\train\labels.cache... 42 images, 0 backgrounds, 0 corrupt: 100%|██████████| 42/42 [00:00<?, ?it/s]Scanning C:\Users\ds678\Downloads\Instance_seg_labels\output_updated_last_time\train\labels.cache... 42 images, 0 backgrounds, 0 corrupt: 100%|██████████| 42/42 [00:00<?, ?it/s]


albumentations: Blur(p=0.01, blur_limit=(3, 7)), MedianBlur(p=0.01, blur_limit=(3, 7)), ToGray(p=0.01), CLAHE(p=0.01, clip_limit=(1, 4.0), tile_grid_size=(8, 8))


val: Scanning C:\Users\ds678\Downloads\Instance_seg_labels\output_updated_last_time\val\labels.cache... 11 images, 0 backgrounds, 0 corrupt: 100%|██████████| 11/11 [00:00<?, ?it/s]Scanning C:\Users\ds678\Downloads\Instance_seg_labels\output_updated_last_time\val\labels.cache... 11 images, 0 backgrounds, 0 corrupt: 100%|██████████| 11/11 [00:00<?, ?it/s]


...

                   all         11        225      0.507      0.457      0.431      0.164      0.459       0.42      0.373      0.146

      Epoch    GPU_mem   box_loss   seg_loss   cls_loss   dfl_loss  Instances       Size


    100/100      7.31G      1.994      1.631      2.212      1.083         83       1536: 100%|██████████| 42/42 [01:50<00:00,  2.62s/it]
                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95)     Mask(P          R      mAP50  mAP50-95): 100%|██████████| 6/6 [00:06<00:00,  1.04s/it]


                   all         11        225        0.5      0.459      0.435      0.159      0.549      0.288      0.384      0.135

100 epochs completed in 2.914 hours.
Optimizer stripped from C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\runs\segment\train6\weights\last.pt, 92.5MB
Optimizer stripped from C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\runs\segment\train6\weights\best.pt, 92.5MB

Validating C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\runs\segment\train6\weights\best.pt...
Ultralytics YOLOv8.2.75  Python-3.10.14 torch-2.4.0+cu121 CUDA:0 (NVIDIA RTX A4000, 16376MiB)
YOLOv8l-seg summary (fused): 295 layers, 45,914,972 parameters, 0 gradients, 220.1 GFLOPs


                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95)     Mask(P          R      mAP50  mAP50-95): 100%|██████████| 6/6 [00:06<00:00,  1.05s/it]


                   all         11        225      0.509      0.458      0.431      0.164      0.461      0.421      0.374      0.146
  ClassicalEvaporation          7        105      0.571      0.292      0.379      0.197       0.44      0.225      0.271     0.0959
    TransitionalMixing          8         61      0.403      0.541      0.395      0.202      0.342      0.459      0.283      0.104
       DiffusiveMixing          6         55          1          0     0.0614     0.0216          1          0     0.0536     0.0201
                 Spray          4          4     0.0615          1      0.888      0.234     0.0615          1      0.888      0.363
Speed: 33.9ms preprocess, 337.3ms inference, 0.0ms loss, 49.6ms postprocess per image
Results saved to C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\runs\segment\train6


## 500 Epochs

In [4]:
results = model.train(data="C:/Users/ds678/OneDrive - University of Sussex/SAF_Project/Instance_seg_labels/custom_data_PC - Copy.yaml", 
                      imgsz=1536, 
                      epochs=500, 
                      task='segment',
                      batch=1, 
                      device=0,
                      patience=0)

New https://pypi.org/project/ultralytics/8.2.79 available  Update with 'pip install -U ultralytics'
Ultralytics YOLOv8.2.75  Python-3.10.14 torch-2.4.0+cu121 CUDA:0 (NVIDIA RTX A4000, 16376MiB)
engine\trainer: task=segment, mode=train, model=yolov8l-seg.yaml, data=C:/Users/ds678/OneDrive - University of Sussex/SAF_Project/Instance_seg_labels/custom_data_PC - Copy.yaml, epochs=500, time=None, patience=0, batch=1, imgsz=1536, save=True, save_period=-1, cache=False, device=0, workers=8, project=None, name=train7, exist_ok=False, pretrained=True, optimizer=auto, verbose=True, seed=0, deterministic=True, single_cls=False, rect=False, cos_lr=False, close_mosaic=10, resume=False, amp=True, fraction=1.0, profile=False, freeze=None, multi_scale=False, overlap_mask=True, mask_ratio=4, dropout=0.0, val=True, split=val, save_json=False, save_hybrid=False, conf=None, iou=0.7, max_det=300, half=False, dnn=False, plots=True, source=None, vid_stride=1, stream_buffer=False, visualize=False, augment=Fal

wandb: Currently logged in as: devanshishah0510 (devanshishah0510-university-of-sussex). Use `wandb login --relogin` to force relogin


Freezing layer 'model.22.dfl.conv.weight'
AMP: running Automatic Mixed Precision (AMP) checks with YOLOv8n...
AMP: checks passed 


C:\ProgramData\anaconda3\envs\instance\lib\site-packages\ultralytics\engine\trainer.py:269: FutureWarning: `torch.cuda.amp.GradScaler(args...)` is deprecated. Please use `torch.amp.GradScaler('cuda', args...)` instead.
  self.scaler = torch.cuda.amp.GradScaler(enabled=self.amp)
train: Scanning C:\Users\ds678\Downloads\Instance_seg_labels\output_updated_last_time\train\labels.cache... 42 images, 0 backgrounds, 0 corrupt: 100%|██████████| 42/42 [00:00<?, ?it/s]Scanning C:\Users\ds678\Downloads\Instance_seg_labels\output_updated_last_time\train\labels.cache... 42 images, 0 backgrounds, 0 corrupt: 100%|██████████| 42/42 [00:00<?, ?it/s]


albumentations: Blur(p=0.01, blur_limit=(3, 7)), MedianBlur(p=0.01, blur_limit=(3, 7)), ToGray(p=0.01), CLAHE(p=0.01, clip_limit=(1, 4.0), tile_grid_size=(8, 8))


...

                   all         11        225      0.311       0.41      0.299      0.176      0.281      0.391      0.222     0.0887

      Epoch    GPU_mem   box_loss   seg_loss   cls_loss   dfl_loss  Instances       Size


    500/500      5.73G      1.248     0.9246      1.221     0.9488         14       1536: 100%|██████████| 42/42 [00:14<00:00,  2.95it/s]
                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95)     Mask(P          R      mAP50  mAP50-95): 100%|██████████| 6/6 [00:02<00:00,  2.39it/s]


                   all         11        225      0.317      0.408      0.295      0.179      0.266      0.419      0.229     0.0881

500 epochs completed in 2.067 hours.
Optimizer stripped from C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\runs\segment\train7\weights\last.pt, 92.6MB
Optimizer stripped from C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\runs\segment\train7\weights\best.pt, 92.5MB

Validating C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\runs\segment\train7\weights\best.pt...
Ultralytics YOLOv8.2.75  Python-3.10.14 torch-2.4.0+cu121 CUDA:0 (NVIDIA RTX A4000, 16376MiB)
YOLOv8l-seg summary (fused): 295 layers, 45,914,972 parameters, 0 gradients, 220.1 GFLOPs


                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95)     Mask(P          R      mAP50  mAP50-95): 100%|██████████| 6/6 [00:01<00:00,  5.61it/s]


                   all         11        225      0.214      0.574      0.392      0.209      0.181      0.521      0.358      0.175
  ClassicalEvaporation          7        105      0.445      0.543      0.483      0.277      0.346       0.41      0.321       0.14
    TransitionalMixing          8         61      0.386      0.754      0.393      0.239      0.351      0.674      0.327      0.139
       DiffusiveMixing          6         55          0          0     0.0584     0.0271          0          0     0.0523     0.0225
                 Spray          4          4     0.0253          1      0.634      0.291     0.0258          1      0.731      0.397
Speed: 3.4ms preprocess, 64.7ms inference, 0.0ms loss, 5.3ms postprocess per image
Results saved to C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\runs\segment\train7


In [6]:
# Load your trained model
model = YOLO("C:/Users/ds678/OneDrive - University of Sussex/SAF_Project/runs/segment/train7/weights/best.pt")

# Run inference on validation dataset
results = model.val(data="C:/Users/ds678/OneDrive - University of Sussex/SAF_Project/Instance_seg_labels/custom_data_PC - Copy.yaml")

Ultralytics YOLOv8.2.75  Python-3.10.14 torch-2.4.0+cu121 CUDA:0 (NVIDIA RTX A4000, 16376MiB)
YOLOv8l-seg summary (fused): 295 layers, 45,914,972 parameters, 0 gradients, 220.1 GFLOPs


val: Scanning C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\Instance_seg_labels\output__SAF2022\val\labels.cache... 11 images, 0 backgrounds, 0 corrupt: 100%|██████████| 11/11 [00:00<?, ?it/s]
                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95)     Mask(P          R      mAP50  mAP50-95): 100%|██████████| 1/1 [00:06<00:00,  6.78s/it]


                   all         11        215       0.29      0.624      0.425      0.221       0.43      0.554      0.414      0.167
  ClassicalEvaporation          7         52      0.317      0.788      0.501      0.327      0.319      0.654      0.417      0.127
    TransitionalMixing          6         82      0.407      0.683      0.403      0.276      0.373      0.561      0.319      0.131
       DiffusiveMixing          6         77      0.412      0.026      0.132      0.068          1          0     0.0749     0.0268
                 Spray          4          4     0.0257          1      0.662      0.213     0.0265          1      0.845      0.384
Speed: 10.5ms preprocess, 78.5ms inference, 0.0ms loss, 1.4ms postprocess per image
Results saved to C:\Users\ds678\OneDrive - University of Sussex\SAF_Project\runs\segment\val11
